In [ ]:
!pip install ultralytics

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 914.7/914.7 kB 21.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 62.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 58.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 43.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 12.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 6.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 83.7 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitlink-cu12
    Found existing installation: nvidia-nvjitlink-cu12 12.5.82
    Uninstall

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
from ultralytics import YOLO
import pandas as pd
import numpy as np
from glob import glob
from tqdm import tqdm
import torch

Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.


In [ ]:
model = YOLO("/content/drive/MyDrive/Endoscope Detection/Yolov11/experiment/v6/train2/weights/best.pt")

In [ ]:
meta_data = pd.read_csv('/content/drive/MyDrive/Endoscope Detection/Yolov11/gastroscopy_meta_256.csv')

In [ ]:
!pip install -q map-boxes
from map_boxes import mean_average_precision_for_boxes

Couldn't import fast version of function compute_overlap, will use slow one. Check cython intallation


In [ ]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(device)

cuda


In [ ]:
img_paths = ["/content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test"]

output_data = []

def format_pred(labels, boxes, scores):
    pred_strings = []
    for label, score, bbox in zip(labels, scores, boxes):
        xmin, ymin, xmax, ymax = bbox.astype(np.float32)
        pred_strings.append(f"{label} {score:.4f} {xmin:.1f} {ymin:.1f} {xmax:.1f} {ymax:.1f}")
    return " ".join(pred_strings)

for img_path in img_paths:
    results = model(img_path, save=True)
    for result in results:
        image_id = result.path.split("/")[-1]
        boxes = result.boxes.xyxy.cpu().numpy()
        scores = result.boxes.conf.cpu().numpy()
        labels = result.boxes.cls.cpu().numpy().astype(int)

        pred_str = format_pred(labels, boxes, scores)
        output_data.append([image_id, pred_str])


image 1/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00021.png: 256x256 1 ulcer, 9.4ms
image 2/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00023.png: 256x256 2 ulcers, 18.5ms
image 3/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00025.png: 256x256 3 ulcers, 9.3ms
image 4/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00033.png: 256x256 (no detections), 16.3ms
image 5/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00035.png: 256x256 2 ulcers, 37.6ms
image 6/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00044.png: 256x256 1 ulcer, 43.3ms
image 7/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00045.png: 256x256 6 ulcers, 28.0ms
image 8/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00142.png: 256x256 3 ulcers, 18.5ms
image 9/400 

In [ ]:
submission_det = pd.DataFrame(output_data, columns=['image_id','PredictionString'])

In [ ]:
submission_det

image_id                                   PredictionString
0    1_1_00021.png                     0 0.5603 21.7 97.8 129.1 207.5
1    1_1_00023.png  0 0.4167 177.1 75.4 250.7 150.7 0 0.2648 106.7...
2    1_1_00025.png  0 0.5324 152.4 78.5 238.9 174.0 0 0.4761 156.9...
3    1_1_00033.png                                                   
4    1_1_00035.png  0 0.4160 111.6 122.0 172.3 166.9 0 0.2782 81.4...
..             ...                                                ...
395  1_3_09783.png                      2 0.9241 0.7 15.6 253.8 238.7
396  1_3_09808.png                     2 0.6431 57.5 25.7 255.2 192.7
397  1_3_09826.png                     2 0.8434 49.9 16.0 254.5 237.7
398  1_3_09872.png  2 0.8629 0.0 18.5 243.6 240.7 2 0.5380 0.0 150...
399  1_3_09997.png                      2 0.9440 0.0 22.1 245.3 229.8

[400 rows x 2 columns]

In [ ]:
def string_decoder(predict_string):
    s = predict_string.split(' ')
    class_id = [x for x in (s[0::6])]
    score = [x for x in (s[1::6])]
    x_min = [x for x in (s[2::6])]
    y_min = [x for x in (s[3::6])]
    x_max = [x for x in (s[4::6])]
    y_max = [x for x in (s[5::6])]

    return class_id, score, x_min, y_min, x_max, y_max

In [ ]:
submission_list = []

for i, row in tqdm(submission_det.iterrows(), total=len(submission_det)):
    image_id = row['image_id']
    string_decoded = string_decoder(row['PredictionString'])

    for  (class_id, score, xmin, ymin, xmax, ymax) in zip(*string_decoded):
        submission_list.append(
            {
                'image_id': image_id,
                'lesion_label': int(class_id),
                'score': float(score),
                'x_min': float(xmin),
                'y_min': float(ymin),
                'x_max': float(xmax),
                'y_max': float(ymax),
                }
        )

submission_metric = pd.DataFrame(submission_list, columns=['image_id', 'lesion_label', 'score','x_min','y_min', 'x_max', 'y_max'])

100%|██████████| 400/400 [00:00<00:00, 17365.74it/s]


In [ ]:
test_id = [x.split('/')[-1] for x in glob('/content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/*.png')]
test_df = meta_data[meta_data['image_id'].isin(test_id)]
test_df = test_df.sort_values(by='image_id').reset_index(drop=True)

In [ ]:
ann = test_df.copy()
det = submission_metric.copy()

ann = ann[['image_id','lesion_label','x_min','x_max','y_min','y_max']].values

det = det[['image_id','lesion_label', 'score','x_min','x_max','y_min','y_max']].values


mean_ap_50, average_precisions_50 = mean_average_precision_for_boxes(ann, det, iou_threshold=0.5)
print("_________________________________________________________")
mean_ap_75, average_precisions_75 = mean_average_precision_for_boxes(ann, det, iou_threshold=0.75)

Number of files in annotations: 398
Number of files in predictions: 379
Unique classes: 3
Detections length: 379
Annotations length: 398
0                              | 0.459410 |     148
1                              | 0.660470 |     270
2                              | 0.712120 |     231
mAP: 0.610666
_________________________________________________________
Number of files in annotations: 398
Number of files in predictions: 379
Unique classes: 3
Detections length: 379
Annotations length: 398
0                              | 0.178228 |     148
1                              | 0.413981 |     270
2                              | 0.468345 |     231
mAP: 0.353518


Finding best conf, IOU, max_box

In [ ]:
def evaluate_model(results):
  output_data = []
  for result in results:
      image_id = result.path.split("/")[-1]
      boxes = result.boxes.xyxy.cpu().numpy()
      scores = result.boxes.conf.cpu().numpy()
      labels = result.boxes.cls.cpu().numpy().astype(int)

      pred_string = format_pred(labels, boxes, scores)
      output_data.append([image_id, pred_string])

  submission_det = pd.DataFrame(output_data, columns=['image_id', 'PredictionString'])

  submission_list = []
  for _, row in tqdm(submission_det.iterrows(), total=len(submission_det)):
      image_id = row['image_id']
      string_decoded = string_decoder(row['PredictionString'])
      for (class_id, score, xmin, ymin, xmax, ymax) in zip(*string_decoded):
          submission_list.append({
              'image_id': image_id,
              'lesion_label': int(class_id),
              'score': float(score),
              'x_min': float(xmin),
              'y_min': float(ymin),
              'x_max': float(xmax),
              'y_max': float(ymax),
          })

  submission_metric = pd.DataFrame(submission_list, columns=['image_id', 'lesion_label', 'score', 'x_min', 'y_min', 'x_max', 'y_max'])

  test_id = [x.split('/')[-1] for x in glob('/content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/*.png')]
  test_df = meta_data[meta_data['image_id'].isin(test_id)]
  test_df = test_df.sort_values(by='image_id').reset_index(drop=True)

  ann = test_df[['image_id', 'lesion_label', 'x_min', 'x_max', 'y_min', 'y_max']].values
  det = submission_metric[['image_id', 'lesion_label', 'score', 'x_min', 'x_max', 'y_min', 'y_max']].values

  mean_ap_50, _ = mean_average_precision_for_boxes(ann, det, iou_threshold=0.5)
  mean_ap_75, _ = mean_average_precision_for_boxes(ann, det, iou_threshold=0.75)

  print(f"mAP@0.5: {mean_ap_50:.4f}, mAP@0.75: {mean_ap_75:.4f}")

  return mean_ap_50, mean_ap_75

In [ ]:
import pandas as pd
from tqdm import tqdm
from glob import glob

conf_values = [0.001, 0.1, 0.3, 0.5, 0.7]
iou_values = [0.3, 0.5, 0.6, 0.7]
max_det_values = [50, 100, 150, 300]

best_score = 0
best_params = {}

for conf in conf_values:
    for iou in iou_values:
        for max_det in max_det_values:
            print(f"conf: {conf}, iou: {iou}, max_det: {max_det}")
            results = model(img_path, conf=conf, iou=iou, max_det=max_det)

            score_50, score_75 = evaluate_model(results)
            score = (score_50 + score_75) / 2

            if score > best_score:
                best_score = score
                best_params = {"conf": conf, "iou": iou, "max_det": max_det}

print(" Best Parameters:", best_params)
print(f" Best Score: {best_score:.4f}")

final_conf = best_params["conf"]
final_iou = best_params["iou"]
final_max_det = best_params["max_det"]

results = model(img_path, conf=final_conf, iou=final_iou, max_det=final_max_det)

output_data = []

for result in results:
    image_id = result.path.split("/")[-1]
    boxes = result.boxes.xyxy.cpu().numpy()
    scores = result.boxes.conf.cpu().numpy()
    labels = result.boxes.cls.cpu().numpy().astype(int)

    pred_string = format_pred(labels, boxes, scores)
    output_data.append([image_id, pred_string])

submission_det = pd.DataFrame(output_data, columns=['image_id', 'PredictionString'])

csv_path = "/content/drive/MyDrive/Endoscope Detection/Yolov11/final_predictions.csv"
submission_det.to_csv(csv_path, index=False)


conf: 0.001, iou: 0.3, max_det: 50

image 1/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00021.png: 256x256 17 ulcers, 3 polyps, 12.1ms
image 2/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00023.png: 256x256 12 ulcers, 1 cancer, 9.4ms
image 3/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00025.png: 256x256 10 ulcers, 7 polyps, 2 cancers, 9.5ms
image 4/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00033.png: 256x256 8 ulcers, 9.5ms
image 5/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00035.png: 256x256 13 ulcers, 32.2ms
image 6/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00044.png: 256x256 4 ulcers, 10.0ms
image 7/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00045.png: 256x256 10 ulcers, 1 polyp, 10.6ms
image 8/400 /content/drive/MyDrive/Endoscope Detect

100%|██████████| 400/400 [00:00<00:00, 13678.94it/s]

Number of files in annotations: 398
Number of files in predictions: 400
Unique classes: 3
Detections length: 400
Annotations length: 398
0                              | 0.548822 |     148


1                              | 0.736518 |     270
2                              | 0.757212 |     231
mAP: 0.680851
Number of files in annotations: 398
Number of files in predictions: 400
Unique classes: 3
Detections length: 400
Annotations length: 398
0                              | 0.173511 |     148
1                              | 0.415182 |     270
2                              | 0.475827 |     231
mAP: 0.354840
mAP@0.5: 0.6809, mAP@0.75: 0.3548
conf: 0.001, iou: 0.3, max_det: 100

image 1/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00021.png: 256x256 17 ulcers, 3 polyps, 18.1ms
image 2/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00023.png: 256x256 12 ulcers, 1 cancer, 16.1ms
image 3/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00025.png: 256x256 10 ulcers, 7 polyps, 2 cancers, 19.0ms
image 4/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_000

100%|██████████| 400/400 [00:00<00:00, 13920.11it/s]

...

Number of files in annotations: 398
Number of files in predictions: 266
Unique classes: 3
Detections length: 266
Annotations length: 398
0                              | 0.209050 |     148
1                              | 0.415146 |     270
2                              | 0.575940 |     231
mAP: 0.400045
Number of files in annotations: 398
Number of files in predictions: 266
Unique classes: 3
Detections length: 266
Annotations length: 398
0                              | 0.115953 |     148
1                              | 0.312491 |     270
2                              | 0.391048 |     231
mAP: 0.273164
mAP@0.5: 0.4000, mAP@0.75: 0.2732
conf: 0.7, iou: 0.7, max_det: 300

image 1/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00021.png: 256x256 (no detections), 15.6ms
image 2/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00023.png: 256x256 (no detections), 13.5ms


image 3/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00025.png: 256x256 (no detections), 15.3ms
image 4/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00033.png: 256x256 (no detections), 17.8ms
image 5/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00035.png: 256x256 (no detections), 15.5ms
image 6/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00044.png: 256x256 1 ulcer, 12.2ms
image 7/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00045.png: 256x256 (no detections), 11.2ms
image 8/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00142.png: 256x256 1 ulcer, 11.8ms
image 9/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00184.png: 256x256 (no detections), 11.7ms
image 10/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00240.png: 256x256

100%|██████████| 400/400 [00:00<00:00, 10914.35it/s]

Number of files in annotations: 398
Number of files in predictions: 266
Unique classes: 3
Detections length: 266
Annotations length: 398
0                              | 0.209050 |     148
1                              | 0.415146 |     270
2                              | 0.575940 |     231
mAP: 0.400045
Number of files in annotations: 398
Number of files in predictions: 266
Unique classes: 3
Detections length: 266
Annotations length: 398
0                              | 0.115953 |     148
1                              | 0.312491 |     270
2                              | 0.391048 |     231
mAP: 0.273164
mAP@0.5: 0.4000, mAP@0.75: 0.2732
 Best Parameters: {'conf': 0.001, 'iou': 0.7, 'max_det': 100}
 Best Score: 0.5380

image 1/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00021.png: 256x256 61 ulcers, 5 polyps, 24.3ms
image 2/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00023.png: 256x256 48 ulcers, 1 cancer, 11.4ms


image 3/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00025.png: 256x256 24 ulcers, 13 polyps, 3 cancers, 13.1ms
image 4/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00033.png: 256x256 29 ulcers, 15.1ms
image 5/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00035.png: 256x256 30 ulcers, 15.8ms
image 6/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00044.png: 256x256 8 ulcers, 14.1ms
image 7/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00045.png: 256x256 20 ulcers, 2 polyps, 16.3ms
image 8/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00142.png: 256x256 27 ulcers, 1 polyp, 1 cancer, 20.0ms
image 9/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/test/1_1_00184.png: 256x256 62 ulcers, 16.7ms
image 10/400 /content/drive/MyDrive/Endoscope Detection/Yolov11/Dataset/images/tes